In [33]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import pickle
import re
import datetime as dt

from pybaseball import *

from sklearn.ensemble import RandomForestClassifier
from sklearn.datasets import make_classification
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import StandardScaler

import psycopg2
import pandas.io.sql as psql
from sqlalchemy import create_engine

pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 200)


In [2]:
df_18 = pd.read_pickle('../pickles/2018_games_labeled.pkl')
df_17 = pd.read_pickle('../pickles/2017_games_labeled.pkl')
df_16 = pd.read_pickle('../pickles/2016_games_labeled.pkl')
df_15 = pd.read_pickle('../pickles/2015_games_labeled.pkl')
merge = pd.read_pickle('../pickles/labeled_games_agg.pkl')

In [77]:
# df_18.to_pickle('../pickles/2018_games_labeled_1.pkl')
# df_17.to_pickle('../pickles/2017_games_labeled_1.pkl')
# df_16.to_pickle('../pickles/2016_games_labeled_1.pkl')
# df_15.to_pickle('../pickles/2015_games_labeled_1.pkl')

In [76]:
print(len(df_18))
df_18.head()

21172


#days   2b   3b    ab   age  appearance_yr  babip   bb    bf   cs  \
95  368.0  0.0  0.0  23.0  45.0              1  0.333  1.0  24.0  0.0   
96  362.0  0.0  0.0   7.0  45.0              2  0.333  0.0   7.0  0.0   
97  360.0  0.0  0.0   9.0  45.0              3  0.250  0.0  10.0  0.0   
98  355.0  1.0  0.0  23.0  45.0              4  0.059  1.0  25.0  0.0   
99  349.0  0.0  0.0  22.0  45.0              5  0.300  1.0  25.0  1.0   

         date  days  days_preceeding  days_rest enddate   er   era  \
95 2018-04-02   9.0              144      182.0     9/1  1.0  1.50   
96 2018-04-08   9.0              138        6.0     9/1  0.0  0.00   
97 2018-04-10   9.0              136        2.0     9/1  1.0  3.00   
98 2018-04-15   9.0              131        5.0     9/1  1.0  1.17   
99 2018-04-21   9.0              125        6.0     9/1  4.0  6.35   

         first_x  first_y    g  gb/fb  gdp   gs    h  hbp   hr  ibb  injured?  \
95  bartolocolon  bartolo  1.0   0.55  1.0  1.0  7.0  0.0  1.0  0.0       0.0   
96  bartolocolon  bartolo  1.0   1.00  0.0  0.0  1.0  0.0  0.0  0.0       0.0   
97  bartolocolon  bartolo  1.0   0.38  0.0  0.0  2.0  0.0  0.0  0.0       0.0   
98  bartolocolon  bartolo  1.0   0.59  0.0  1.0  1.0  0.0  0.0  0.0       0.0   
99  bartolocolon  bartolo  1.0   0.52  0.0  1.0  7.0  1.0  1.0  0.0       0.0   

   injury   ip key_bbref_x key_bbref_y  key_fangraphs_x  key_fangraphs_y  \
95   Back  6.0   colonba01   colonba01            375.0            375.0   
96   Back  2.0   colonba01   colonba01            375.0            375.0   
97   Back  3.0   colonba01   colonba01            375.0            375.0   
98   Back  7.2   colonba01   colonba01            375.0            375.0   
99   Back  5.2   colonba01   colonba01            375.0            375.0   

    key_mlbam key_retro_x key_retro_y   l        last_x last_y    ld     lev  \
95   112526.0    colob001    colob001 NaN  bartolocolon  colon  0.10  MLB-AL   
96   112526.0    colob001    colob001 NaN  bartolocolon  colon  0.00  MLB-AL   
97   112526.0    colob001    colob001 NaN  bartolocolon  colon  0.25  MLB-AL   
98   112526.0    colob001    colob001 NaN  bartolocolon  colon  0.18  MLB-AL   
99   112526.0    colob001    colob001 NaN  bartolocolon  colon  0.24  MLB-AL   

   list  mlb_played_first_x  mlb_played_first_y  mlb_played_last_x  \
95  10               1997.0              1997.0             2018.0   
96  10               1997.0              1997.0             2018.0   
97  10               1997.0              1997.0             2018.0   
98  10               1997.0              1997.0             2018.0   
99  10               1997.0              1997.0             2018.0   

    mlb_played_last_y moneyearned name_first_x name_first_y name_last_x  \
95             2018.0       84681      bartolo      bartolo       colon   
96             2018.0       84681      bartolo      bartolo       colon   
97             2018.0       84681      bartolo      bartolo       colon   
98             2018.0       84681      bartolo      bartolo       colon   
99             2018.0       84681      bartolo      bartolo       colon   

   name_last_y        name_x        name_y   pit   po posititon    pu    r  \
95       colon  bartolocolon  bartolocolon  89.0  0.0        SP  0.05  1.0   
96       colon  bartolocolon  bartolocolon  29.0  0.0        SP  0.00  0.0   
97       colon  bartolocolon  bartolocolon  29.0  0.0        SP  0.00  1.0   
98       colon  bartolocolon  bartolocolon  96.0  0.0        SP  0.00  1.0   
99       colon  bartolocolon  bartolocolon  85.0  0.0        SP  0.00  4.0   

     sb   sf   so  so/w   so9  startdate   stl   str   sts  sv team     tm  \
95  0.0  0.0  4.0   4.0   6.0 2018-08-24  0.21  0.70  0.07 NaN  TEX  Texas   
96  0.0  0.0  4.0   NaN  18.0 2018-08-24  0.24  0.72  0.14 NaN  TEX  Texas   
97  0.0  1.0  2.0   NaN   6.0 2018-08-24  0.14  0.66  0.10 NaN  TEX  Texas   
98  0.0  1.0  7.0   7.0   8.2 2018-08-24  0.24  0.69  0.08 NaN  TE

In [75]:
df_18 = merge[merge['date'] >= "2018-03-29"]

In [9]:
print(len(df_17))
df_17 = merge[merge['date'] >= "2017-03-01"]
df_17 = df_17[df_17['date'] <= "2017-11-01"]
df_17

20498


#days   2b   3b    ab   age  appearance_yr  babip   bb    bf   cs  \
67     730.0  0.0  0.0  20.0  44.0              1  0.077  1.0  21.0  0.0   
68     724.0  0.0  0.0  16.0  44.0              2  0.400  2.0  20.0  0.0   
69     719.0  0.0  0.0  21.0  44.0              3  0.000  1.0  22.0  0.0   
70     714.0  4.0  0.0  30.0  44.0              4  0.423  1.0  32.0  0.0   
71     707.0  4.0  0.0  23.0  44.0              5  0.500  2.0  25.0  0.0   
72     702.0  4.0  0.0  17.0  44.0              6  0.412  2.0  20.0  0.0   
73     696.0  1.0  1.0  26.0  44.0              7  0.250  0.0  26.0  0.0   
74     690.0  3.0  0.0  22.0  44.0              8  0.333  2.0  24.0  0.0   
75     685.0  0.0  0.0  20.0  44.0              9  0.500  0.0  20.0  1.0   
76     680.0  3.0  0.0  23.0  44.0             10  0.429  3.0  27.0  0.0   
77     675.0  0.0  0.0  19.0  44.0             11  0.375  1.0  20.0  0.0   
78     669.0  4.0  0.0  16.0  44.0             12  0.545  2.0  19.0  0.0   
79     646.0  1.0  1.0  19.0  44.0             13  0.471  3.0  23.0  0.0   
80     626.0  2.0  0.0  20.0  44.0             14  0.471  0.0  20.0  0.0   
81     620.0  0.0  1.0  20.0  44.0             15  0.375  0.0  21.0  0.0   
82     614.0  3.0  0.0  26.0  44.0             16  0.280  1.0  28.0  0.0   
83     609.0  4.0  0.0  35.0  44.0             17  0.276  1.0  36.0  0.0   
84     604.0  0.0  0.0  25.0  44.0             18  0.250  1.0  27.0  0.0   
85     598.0  1.0  0.0  21.0  44.0             19  0.267  4.0  25.0  0.0   
86     593.0  2.0  0.0  24.0  44.0             20  0.267  2.0  26.0  0.0   
87     588.0  1.0  0.0  29.0  44.0             21  0.286  1.0  30.0  0.0   
88     582.0  2.0  0.0  27.0  44.0             22  0.526  0.0  27.0  1.0   
89     577.0  1.0  0.0  26.0  44.0             23  0.200  1.0  27.0  0.0   
90     572.0  3.0  0.0  11.0  44.0             24  0.545  0.0  11.0  0.0   
91     567.0  2.0  0.0  23.0  44.0             25  0.150  2.0  25.0  0.0   
92     562.0  3.0  1.0  17.0  44.0             26  0.417  1.0  18.0  0.0   
93     556.0  1.0  0.0   6.0  44.0             27  0.600  0.0   6.0  0.0   
94     551.0  1.0  0.0  21.0  44.0             28  0.125  1.0  22.0  0.0   
362    732.0  0.0  0.0   4.0  40.0              1  0.000  0.0   4.0  0.0   
363    729.0  0.0  0.0   2.0  40.0              2    NaN  0.0   2.0  0.0   
364    727.0  0.0  0.0   4.0  40.0              3  0.333  1.0   5.0  0.0   
365    724.0  1.0  0.0   4.0  40.0              4  0.250  0.0   4.0  0.0   
366    721.0  0.0  0.0   4.0  40.0              5  0.000  1.0   5.0  0.0   
367    716.0  0.0  0.0   4.0  40.0              6  0.333  1.0   5.0  0.0   
368    715.0  1.0  0.0   4.0  40.0              7  0.500  2.0   6.0  0.0   
369    711.0  0.0  0.0   3.0  40.0              8  0.000  0.0   3.0  0.0   
370    710.0  0.0  0.0   3.0  40.0              9    NaN  0.0   3.0  0.0   
371    707.0  0.0  0.0   2.0  40.0             10    NaN  1.0   3.0  0.0   
372    703.0  1.0  0.0   2.0  40.0             11  1.000  1.0   3.0  0.0   
373    699.0  0.0  0.0   4.0  40.0             12  0.000  2.0   6.0  0.0   
374    696.0  0.0  0.0   1.0  40.0             13    NaN  0.0   1.0  0.0   
375    694.0  1.0  0.0   5.0  40.0             14  0.500  0.0   5.0  0.0   
376    692.0  0.0  0.0   3.0  40.0             15  0.667  0.0   3.0  0.0   
377    690.0  0.0  0.0   3.0  40.0             16  0.000  0.0   3.0  0.0   
378    687.0  0.0  0.0   3.0  40.0             17  0.000  0.0   3.0  0.0   
379    686.0  0.0  0.0   4.0  40.0             18  1.000  0.0   4.0  0.0   
380    681.0  1.0  0.0   4.0  40.0             19  0.250  0.0   4.0  0.0   
381    677.0  0.0  0.0   3.0  40.0             20  0.000  0.0   3.0  0.0   
382    674.0  0.0  0.0   4.0  40.0             21  0.333  0.0   4.0  0.0   
383    671.0  0.0  0.0   6.0  40.0             22  0.000  0.0   6.0  0.0   
384    661.0  0.0  0.0   3.0  40.0             23  0.333  0.0   3.0  0.0   
385    658.0  0.0  0.0   3.0  40.0             24  0.00

In [13]:
print(len(df_16))
df_16 = merge[merge['date'] <= "2016-11-01"]
df_16 = df_16[df_16['date'] >= "2016-03-01"]
df_16

20148


#days   2b   3b    ab   age  appearance_yr  babip   bb    bf   cs  \
33     1097.0  0.0  0.0   5.0  43.0              1  0.250  0.0   5.0  0.0   
34     1091.0  1.0  0.0  21.0  43.0              2  0.308  0.0  21.0  1.0   
35     1085.0  3.0  0.0  25.0  43.0              3  0.400  1.0  26.0  0.0   
36     1080.0  0.0  0.0  20.0  43.0              4  0.188  1.0  23.0  0.0   
37     1074.0  1.0  0.0  19.0  43.0              5  0.467  1.0  22.0  2.0   
38     1068.0  2.0  0.0  29.0  43.0              6  0.318  0.0  30.0  0.0   
39     1063.0  0.0  0.0  25.0  43.0              7  0.263  1.0  27.0  0.0   
40     1058.0  0.0  0.0  22.0  43.0              8  0.294  0.0  22.0  0.0   
41     1052.0  0.0  0.0  18.0  43.0              9  0.357  5.0  24.0  0.0   
42     1047.0  0.0  0.0  25.0  43.0             10  0.217  2.0  27.0  0.0   
43     1041.0  1.0  0.0  26.0  43.0             11  0.304  1.0  27.0  0.0   
44     1035.0  1.0  0.0  20.0  43.0             12  0.222  1.0  21.0  0.0   
45     1030.0  2.0  0.0  25.0  43.0             13  0.348  0.0  25.0  1.0   
46     1023.0  2.0  0.0  28.0  43.0             14  0.316  0.0  28.0  0.0   
47     1018.0  0.0  0.0   1.0  43.0             15  0.000  0.0   1.0  0.0   
48     1013.0  2.0  0.0  27.0  43.0             16  0.208  1.0  28.0  0.0   
49     1007.0  0.0  0.0  22.0  43.0             17  0.188  3.0  25.0  0.0   
50     1002.0  0.0  1.0  23.0  43.0             18  0.389  0.0  23.0  0.0   
51      994.0  0.0  1.0  22.0  43.0             19  0.222  2.0  24.0  0.0   
52      989.0  2.0  0.0  20.0  43.0             20  0.353  2.0  24.0  0.0   
53      983.0  1.0  0.0  23.0  43.0             21  0.143  0.0  23.0  0.0   
54      979.0  2.0  0.0  22.0  43.0             22  0.353  1.0  23.0  0.0   
55      974.0  1.0  0.0  26.0  43.0             23  0.240  0.0  26.0  0.0   
56      968.0  3.0  0.0  26.0  43.0             24  0.389  1.0  27.0  2.0   
57      963.0  3.0  1.0  19.0  43.0             25  0.474  2.0  23.0  1.0   
58      958.0  1.0  1.0  26.0  43.0             26  0.400  1.0  27.0  0.0   
59      952.0  3.0  0.0  27.0  43.0             27  0.286  2.0  29.0  0.0   
60      947.0  1.0  0.0  29.0  43.0             28  0.240  0.0  29.0  0.0   
61      942.0  1.0  1.0  21.0  43.0             29  0.263  1.0  22.0  0.0   
62      937.0  1.0  0.0  21.0  43.0             30  0.111  1.0  24.0  0.0   
63      931.0  0.0  0.0  23.0  43.0             31  0.176  2.0  25.0  0.0   
64      926.0  0.0  0.0  26.0  43.0             32  0.263  0.0  26.0  0.0   
65      921.0  2.0  1.0  14.0  43.0             33  0.538  0.0  15.0  0.0   
66      916.0  0.0  0.0  19.0  43.0             34  0.333  0.0  19.0  0.0   
176     985.0  0.0  1.0   4.0  41.0              1  1.000  1.0   5.0  0.0   
177     983.0  0.0  0.0   3.0  41.0              2  0.000  0.0   3.0  0.0   
178     978.0  1.0  0.0   1.0  41.0              3  1.000  1.0   2.0  0.0   
179     943.0  0.0  0.0   3.0  41.0              4  0.000  0.0   3.0  0.0   
180     940.0  1.0  0.0   2.0  41.0              5  1.000  0.0   2.0  0.0   
181     938.0  0.0  0.0   4.0  41.0              6  0.333  0.0   4.0  0.0   
182     933.0  0.0  0.0   2.0  41.0              7  0.000  2.0   4.0  0.0   
183     929.0  0.0  0.0   1.0  41.0              8  0.000  0.0   1.0  0.0   
184     924.0  0.0  0.0   3.0  41.0              9  0.000  0.0   3.0  0.0   
185     920.0  0.0  0.0   1.0  41.0             10    NaN  0.0   1.0  0.0   
295    1096.0  0.0  0.0   4.0  39.0              1  0.500  1.0   6.0  0.0   
296    1091.0  0.0  0.0   2.0  39.0              2  0.000  3.0   5.0  0.0   
297    1089.0  0.0  0.0   3.0  39.0              3  0.000  0.0   3.0  0.0   
298    1084.0  0.0  0.0   4.0  39.0              4  1.000  1.0   5.0  0.0   
299    1083.0  0.0  0.0   5.0  39.0              5  0.500  0.0   5.0  0.0   
300    1080.0  1.0  0.0   3.0  39.0              6  1.000  2.0   5.0  0.0   
301    1078.0  0.0  0.0   3.0  39.0              7  0.333  0.0   3.0  0.0   
302 

In [14]:
print(len(df_15))
df_15 = merge[merge['date'] <= '2015-11-01']
df_15

19945


#days   2b   3b    ab   age  appearance_yr  babip   bb    bf   cs  \
0      1460.0  0.0  0.0  22.0  42.0              1  0.154  1.0  23.0  0.0   
1      1454.0  1.0  1.0  27.0  42.0              2  0.238  0.0  27.0  0.0   
2      1449.0  2.0  0.0  26.0  42.0              3  0.250  0.0  26.0  0.0   
3      1443.0  2.0  0.0  23.0  42.0              4  0.368  0.0  24.0  1.0   
4      1437.0  2.0  0.0  26.0  42.0              5  0.333  0.0  29.0  0.0   
5      1431.0  0.0  0.0  29.0  42.0              6  0.263  0.0  29.0  0.0   
6      1426.0  3.0  0.0  26.0  42.0              7  0.368  0.0  26.0  0.0   
7      1421.0  4.0  0.0  23.0  42.0              8  0.263  0.0  23.0  0.0   
8      1416.0  2.0  0.0  24.0  42.0              9  0.500  2.0  27.0  0.0   
9      1411.0  1.0  0.0  23.0  42.0             10  0.333  2.0  26.0  0.0   
10     1405.0  1.0  0.0  26.0  42.0             11  0.217  0.0  27.0  0.0   
11     1399.0  0.0  0.0  25.0  42.0             12  0.235  1.0  26.0  0.0   
12     1393.0  2.0  0.0  23.0  42.0             13  0.300  2.0  27.0  0.0   
13     1387.0  1.0  0.0  23.0  42.0             14  0.444  1.0  24.0  0.0   
14     1381.0  3.0  0.0  27.0  42.0             15  0.391  1.0  28.0  0.0   
15     1374.0  2.0  0.0  24.0  42.0             16  0.188  1.0  25.0  0.0   
16     1368.0  0.0  0.0  28.0  42.0             17  0.400  0.0  29.0  0.0   
17     1357.0  4.0  0.0  21.0  42.0             18  0.500  3.0  25.0  0.0   
18     1352.0  0.0  0.0  26.0  42.0             19  0.190  0.0  27.0  0.0   
19     1346.0  0.0  0.0  15.0  42.0             20  0.615  0.0  17.0  0.0   
20     1341.0  2.0  0.0  31.0  42.0             21  0.269  0.0  31.0  0.0   
21     1335.0  2.0  0.0  26.0  42.0             22  0.308  0.0  28.0  0.0   
22     1330.0  0.0  0.0  24.0  42.0             23  0.250  2.0  26.0  0.0   
23     1323.0  2.0  0.0  19.0  42.0             24  0.400  2.0  22.0  0.0   
24     1318.0  1.0  0.0  25.0  42.0             25  0.294  2.0  28.0  0.0   
25     1315.0  1.0  0.0   4.0  42.0             26  0.500  0.0   4.0  0.0   
26     1313.0  0.0  0.0  27.0  42.0             27  0.222  1.0  28.0  0.0   
27     1308.0  1.0  0.0  33.0  42.0             28  0.290  0.0  33.0  0.0   
28     1303.0  0.0  1.0  26.0  42.0             29  0.292  1.0  27.0  0.0   
29     1297.0  2.0  0.0  21.0  42.0             30  0.278  1.0  23.0  1.0   
30     1290.0  0.0  0.0  23.0  42.0             31  0.227  1.0  25.0  0.0   
31     1284.0  0.0  0.0  22.0  42.0             32  0.389  0.0  22.0  0.0   
32     1279.0  0.0  0.0   3.0  42.0             33  0.000  0.0   3.0  0.0   
123    1459.0  0.0  0.0   4.0  42.0              1  0.333  0.0   4.0  0.0   
124    1458.0  0.0  0.0   7.0  42.0              2  0.667  0.0   7.0  0.0   
125    1454.0  0.0  0.0   4.0  42.0              3  1.000  1.0   5.0  0.0   
126    1452.0  0.0  0.0   3.0  42.0              4  0.000  0.0   3.0  0.0   
127    1449.0  0.0  0.0   3.0  42.0              5  0.000  1.0   4.0  0.0   
128    1446.0  0.0  0.0   3.0  42.0              6  1.000  0.0   3.0  0.0   
129    1445.0  0.0  0.0   5.0  42.0              7  0.400  0.0   5.0  0.0   
130    1394.0  0.0  0.0   5.0  42.0              8  0.500  0.0   5.0  0.0   
131    1392.0  0.0  0.0   3.0  42.0              9  0.000  0.0   3.0  0.0   
132    1390.0  0.0  0.0   5.0  42.0             10  0.333  1.0   6.0  0.0   
133    1387.0  0.0  0.0   3.0  42.0             11  0.000  0.0   3.0  0.0   
134    1386.0  0.0  0.0   3.0  42.0             12  0.500  0.0   3.0  0.0   
135    1382.0  0.0  0.0   5.0  42.0             13  0.500  0.0   5.0  0.0   
136    1381.0  0.0  0.0   1.0  42.0             14  0.000  0.0   1.0  0.0   
137    1377.0  0.0  0.0   1.0  42.0             15    NaN  0.0   1.0  0.0   
138    1375.0  0.0  0.0   3.0  42.0             16  0.000  0.0   3.0  0.0   
139    1371.0  0.0  0.0   3.0  42.0             17  0.000  0.0   3.0  0.0   
140    1370.0  0.0  0.0   3.0  42.0             18  0.000  0.0   3.0  0.0   
141 

In [15]:
def pitches_season(year):
    march = statcast('{}-03-01'.format(year), '{}-03-31'.format(year))
    april = statcast('{}-04-01'.format(year), '{}-04-30'.format(year))
    may = statcast('{}-05-01'.format(year), '{}-05-31'.format(year))
    june = statcast('{}-06-01'.format(year), '{}-06-30'.format(year))
    july = statcast('{}-07-01'.format(year), '{}-07-31'.format(year))
    aug = statcast('{}-08-01'.format(year), '{}-08-31'.format(year))
    sept = statcast('{}-09-01'.format(year), '{}-09-30'.format(year))
    octo = statcast('{}-10-01'.format(year), '{}-10-31'.format(year))
    nov = statcast('{}-11-01'.format(year), '{}-11-30'.format(year))

    total = pd.concat([march,april,may,june,july,aug,sept,octo,nov])
    print(len(total))
    copy = total.dropna(subset=['pitch_type'])
    print(len(copy))
    copy['game_date'] = pd.to_datetime(copy['game_date'])

    return copy


In [16]:
# sc_17 = pitches_season(2017)

This is a large query, it may take a moment to complete
Completed sub-query from 2017-03-01 to 2017-03-31
This is a large query, it may take a moment to complete
Completed sub-query from 2017-04-01 to 2017-04-06
Completed sub-query from 2017-04-07 to 2017-04-12
Completed sub-query from 2017-04-13 to 2017-04-18
Completed sub-query from 2017-04-19 to 2017-04-24
Completed sub-query from 2017-04-25 to 2017-04-30


KeyError: "['release_speed' 'release_pos_x' 'release_pos_z' 'batter' 'pitcher' 'zone'\n 'hit_location' 'balls' 'strikes' 'game_year' 'pfx_x' 'pfx_z' 'plate_x'\n 'plate_z' 'on_3b' 'on_2b' 'on_1b' 'outs_when_up' 'inning' 'hc_x' 'hc_y'\n 'fielder_2' 'vx0' 'vy0' 'vz0' 'ax' 'ay' 'az' 'sz_top' 'sz_bot'\n 'hit_distance_sc' 'launch_speed' 'launch_angle' 'effective_speed'\n 'release_spin_rate' 'release_extension' 'game_pk' 'pitcher.1'\n 'fielder_2.1' 'fielder_3' 'fielder_4' 'fielder_5' 'fielder_6' 'fielder_7'\n 'fielder_8' 'fielder_9' 'release_pos_y' 'estimated_ba_using_speedangle'\n 'estimated_woba_using_speedangle' 'woba_value' 'woba_denom' 'babip_value'\n 'iso_value' 'launch_speed_angle' 'at_bat_number' 'pitch_number'\n 'home_score' 'away_score' 'bat_score' 'fld_score' 'post_away_score'\n 'post_home_score' 'post_bat_score' 'post_fld_score'] not in index"

In [68]:
2895090- 2182878

712212

In [51]:
march = statcast('2015-03-01', '2015-03-31')

This is a large query, it may take a moment to complete
Completed sub-query from 2015-03-01 to 2015-03-31


In [52]:
april = statcast('2015-04-01', '2015-04-30')

This is a large query, it may take a moment to complete
Completed sub-query from 2015-04-01 to 2015-04-06
Completed sub-query from 2015-04-07 to 2015-04-12
Completed sub-query from 2015-04-13 to 2015-04-18
Completed sub-query from 2015-04-19 to 2015-04-24
Completed sub-query from 2015-04-25 to 2015-04-30


In [53]:
may =  statcast('2015-05-01', '2015-05-31')

This is a large query, it may take a moment to complete
Completed sub-query from 2015-05-01 to 2015-05-06
Completed sub-query from 2015-05-07 to 2015-05-12
Completed sub-query from 2015-05-13 to 2015-05-18
Completed sub-query from 2015-05-19 to 2015-05-24
Completed sub-query from 2015-05-25 to 2015-05-30
Completed sub-query from 2015-05-31 to 2015-05-31


In [54]:
june = statcast('2015-06-01', '2015-06-30')

This is a large query, it may take a moment to complete
Completed sub-query from 2015-06-01 to 2015-06-06
Completed sub-query from 2015-06-07 to 2015-06-12
Completed sub-query from 2015-06-13 to 2015-06-18
Completed sub-query from 2015-06-19 to 2015-06-24
Completed sub-query from 2015-06-25 to 2015-06-30


In [55]:
july = statcast('2015-07-01', '2015-07-31')

This is a large query, it may take a moment to complete
Completed sub-query from 2015-07-01 to 2015-07-06
Completed sub-query from 2015-07-07 to 2015-07-12
Completed sub-query from 2015-07-13 to 2015-07-18
Completed sub-query from 2015-07-19 to 2015-07-24
Completed sub-query from 2015-07-25 to 2015-07-30
Completed sub-query from 2015-07-31 to 2015-07-31


In [56]:
aug = statcast('2015-08-01', '2015-08-31')

This is a large query, it may take a moment to complete
Completed sub-query from 2015-08-01 to 2015-08-06
Completed sub-query from 2015-08-07 to 2015-08-12
Completed sub-query from 2015-08-13 to 2015-08-18
Completed sub-query from 2015-08-19 to 2015-08-24
Completed sub-query from 2015-08-25 to 2015-08-30
Completed sub-query from 2015-08-31 to 2015-08-31


In [60]:
sept = statcast('2015-09-01', '2015-09-30')

This is a large query, it may take a moment to complete
Completed sub-query from 2015-09-01 to 2015-09-06
Completed sub-query from 2015-09-07 to 2015-09-12
Completed sub-query from 2015-09-13 to 2015-09-18
Completed sub-query from 2015-09-19 to 2015-09-24
Completed sub-query from 2015-09-25 to 2015-09-30


In [61]:
octo = statcast('2015-10-01', '2015-10-31')

This is a large query, it may take a moment to complete
Completed sub-query from 2015-10-01 to 2015-10-06
Completed sub-query from 2015-10-07 to 2015-10-12
Completed sub-query from 2015-10-13 to 2015-10-18
Completed sub-query from 2015-10-19 to 2015-10-24
Completed sub-query from 2015-10-25 to 2015-10-30
Completed sub-query from 2015-10-31 to 2015-10-31


In [62]:
nov = statcast('2015-11-01', '2015-11-30')

This is a large query, it may take a moment to complete
Completed sub-query from 2015-11-01 to 2015-11-06
Query unsuccessful for data from 2015-11-07 to 2015-11-11. Skipping these dates.
Query unsuccessful for data from 2015-11-12 to 2015-11-12. Skipping these dates.
Query unsuccessful for data from 2015-11-13 to 2015-11-17. Skipping these dates.
Query unsuccessful for data from 2015-11-18 to 2015-11-18. Skipping these dates.
Completed sub-query from 2015-11-19 to 2015-11-30


In [63]:
total = pd.concat([march,april,may,june,july,aug,sept,octo,nov])
print(len(total))

712840


In [64]:
copy = total.dropna(subset=['pitch_type'])
print(len(copy))

712212


In [65]:
copy['game_date'] = pd.to_datetime(copy['game_date'])

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [66]:
copy

index pitch_type  game_date  release_speed  release_pos_x  release_pos_z  \
0      24         SL 2015-04-30           84.7        -1.7969         5.7847   
1      26         SL 2015-04-30           83.1        -1.9585         5.8173   
2      32         FF 2015-04-30           94.5        -1.9104         5.9743   
3      34         SI 2015-04-30           94.4        -1.8113         5.6788   
4      40         FF 2015-04-30           95.4        -1.8972         5.7889   
5      42         SL 2015-04-30           84.7        -1.7287         5.8388   
6      46         SI 2015-04-30           93.9        -1.9462         5.6715   
7      52         SL 2015-04-30           82.9        -1.9693         5.8454   
8      54         FF 2015-04-30           94.5        -1.8995         5.9458   
9      58         FF 2015-04-30           93.4         0.9713         6.1978   
10     64         FF 2015-04-30           93.2         1.0613         6.0723   
11     66         FF 2015-04-30           94.1         0.9987         6.1837   
12     72         FF 2015-04-30           92.3         1.1969         6.0529   
13     74         FF 2015-04-30           93.8         1.1346         6.2115   
14     82         FF 2015-04-30           93.6         1.0549         6.1456   
15     84         FF 2015-04-30           93.3         1.1453         6.1059   
16     91         FF 2015-04-30           93.8         1.0409         6.1090   
17     98         FF 2015-04-30           92.3         1.0738         6.1680   
18    100         FF 2015-04-30           92.9         1.0571         6.0721   
19    104         FF 2015-04-30           91.3        -1.2261         5.7385   
20    112         FF 2015-04-30           90.3        -1.3917         5.6421   
21    114         SL 2015-04-30           86.5        -1.3052         5.7498   
22    122         FF 2015-04-30           89.4        -1.1715         5.9691   
23    126         FF 2015-04-30           90.7        -1.1625         5.7812   
24    134         FF 2015-04-30           91.5        -0.9700         6.0148   
25    142         SI 2015-04-30           89.7        -1.1630         5.7502   
26    144         SL 2015-04-30           86.2        -1.3829         5.7538   
27    152         SI 2015-04-30           89.3        -1.3246         5.6745   
28    164         CH 2015-04-30           84.3        -1.1824         6.1641   
29    166         SI 2015-04-30           90.2        -1.3543         5.6993   
30    178         KC 2015-04-30           83.8         1.9937         6.4742   
31    184         KC 2015-04-30           82.8         2.0381         6.5580   
32    192         SI 2015-04-30           95.2         2.0151         6.5160   
33    200         SI 2015-04-30           94.0         1.9464         6.5976   
34    210         SI 2015-04-30           94.9         2.0920         6.4775   
35    214         CH 2015-04-30           84.5         1.8007         6.5069   
36    227         SI 2015-04-30           94.4         2.1134         6.5726   
37    237         SI 2015-04-30           94.9         1.9641         6.5587   
38    239         KC 2015-04-30           82.4         1.8995         6.6847   
39    250         SI 2015-04-30           94.8         2.0130         6.6884   
40    254         SI 2015-04-30           93.6         1.9765         6.5835   
41    267         CH 2015-04-30           82.3         1.9272         6.7182   
42    275         FF 2015-04-30           92.3        -1.1488         5.7474   
43    279         SI 2015-04-30           91.1        -1.1782         5.8293   
44    287         FF 2015-04-30           92.2        -1.1524         5.7240   
45    300         CH 2015-04-30           84.1        -1.0422         6.1600   
46    305         FF 2015-04-30           91.7        -1.2950         5.7722   
47    316         SL 2015-04-30           85.6        -1.3563         5.8071   
48    319         SL 2015-04-30           87.2        -1.4692         5.7413   
49  

In [67]:
# engine = create_engine('postgresql+psycopg2://taylorphillips@localhost/statcast')

# copy.to_sql('pitches', engine, if_exists='append')

In [109]:
conn = psycopg2.connect(dbname='statcast', user='taylorphillips', host='localhost')
cur = conn.cursor()

return_frame = pd.DataFrame()

id_list = df_15['key_mlbam'].unique().tolist()

for id in id_list:
    fastballs = psql.read_sql('''
    SELECT COUNT(pitch_type) as {0}_count, game_date as date, p_throws, AVG(release_speed) as {0}_release_speed,
    AVG(effective_speed) as {0}_percieved_speed, AVG(release_spin_rate) as {0}_spin_rate, 
    AVG(release_pos_x) as {0}_avg_x, AVG(release_pos_z) as {0}_avg_z, AVG(release_extension) as {0}_avg_extension,
    AVG(pfx_x) as {0}_x_movement, AVG(pfx_z) as {0}_z_movement 
    FROM pitches 
    WHERE pitcher = {1} AND pitch_type IN ('FF','FT', 'SI') AND game_date >= '2015-03-01' AND game_date <= '2015-11-01'
    GROUP BY date, p_throws
    ORDER BY date
    '''.format('fb', id), conn)

#     fastballs = psql.read_sql('''
#     SELECT COUNT(pitch_type) as {0}_count, game_date as date, p_throws
#     FROM pitches 
#     WHERE pitcher = {1} AND pitch_type IN ('FF','FT', 'SI')
#     GROUP BY date, p_throws
#     ORDER BY date
#     '''.format('fb', id), conn)
    
    offspeed = psql.read_sql('''
    SELECT COUNT(pitch_type) as {0}_count, game_date as date, p_throws, AVG(release_speed) as {0}_release_speed,
    AVG(effective_speed) as {0}_percieved_speed, AVG(release_spin_rate) as {0}_spin_rate, 
    AVG(release_pos_x) as {0}_avg_x, AVG(release_pos_z) as {0}_avg_z, AVG(release_extension) as {0}_avg_extension,
    AVG(pfx_x) as {0}_x_movement, AVG(pfx_z) as {0}_z_movement 
    FROM pitches 
    WHERE pitcher = {1} AND pitch_type IN ('FC', 'SL', 'FS', 'CH', 'KC', 'CU', 'FO', 'KN', 'SC', 'EP')
    AND game_date >= '2015-03-01' AND game_date <= '2015-11-01'
    GROUP BY date, p_throws
    ORDER BY date
    '''.format('os', id), conn)
    
    frame = df_15[df_15['key_mlbam'] == id]
    
    fb_frame = frame.merge(fastballs, on='date', how='left')
    merge_frame = fb_frame.merge(offspeed, on='date', how='left')
    return_frame = return_frame.append(merge_frame)

In [110]:
#  AND game_date >= '2018-03-01' AND game_date <= '2018-11-01'
drop = ['#days', '2b', '3b', 'ab', 'babip', 'bf', 'cs', 'date', 'days', 'days_preceeding', 'enddate', 'era', 'first_x', 'first_y', 'g', 'gb/fb', 'gdp', 'gs', 'ibb', 'injury', 'key_bbref_x', 'key_bbref_y', 'key_fangraphs_x', 'key_fangraphs_y', 'key_mlbam', 'key_retro_x', 'key_retro_y', 'l', 'last_x', 'last_y', 'ld', 'lev', 'list', 'mlb_played_first_y', 'mlb_played_last_x', 'mlb_played_last_y', 'moneyearned', 'name_first_x', 'name_first_y', 'name_last_x', 'name_last_y', 'name_x', 'name_y', 'po', 'posititon', 'pu', 'sb', 'sf', 'startdate', 'stl', 'sts', 'sv', 'team', 'tm', 'year', 'p_throws_y']

In [111]:
print(len(df_15))
print(len(return_frame))
return_frame

19945
20004


#days   2b   3b    ab   age  appearance_yr  babip   bb    bf   cs  \
0   1460.0  0.0  0.0  22.0  42.0              1  0.154  1.0  23.0  0.0   
1   1454.0  1.0  1.0  27.0  42.0              2  0.238  0.0  27.0  0.0   
2   1449.0  2.0  0.0  26.0  42.0              3  0.250  0.0  26.0  0.0   
3   1443.0  2.0  0.0  23.0  42.0              4  0.368  0.0  24.0  1.0   
4   1437.0  2.0  0.0  26.0  42.0              5  0.333  0.0  29.0  0.0   
5   1431.0  0.0  0.0  29.0  42.0              6  0.263  0.0  29.0  0.0   
6   1426.0  3.0  0.0  26.0  42.0              7  0.368  0.0  26.0  0.0   
7   1421.0  4.0  0.0  23.0  42.0              8  0.263  0.0  23.0  0.0   
8   1416.0  2.0  0.0  24.0  42.0              9  0.500  2.0  27.0  0.0   
9   1411.0  1.0  0.0  23.0  42.0             10  0.333  2.0  26.0  0.0   
10  1405.0  1.0  0.0  26.0  42.0             11  0.217  0.0  27.0  0.0   
11  1399.0  0.0  0.0  25.0  42.0             12  0.235  1.0  26.0  0.0   
12  1393.0  2.0  0.0  23.0  42.0             13  0.300  2.0  27.0  0.0   
13  1387.0  1.0  0.0  23.0  42.0             14  0.444  1.0  24.0  0.0   
14  1381.0  3.0  0.0  27.0  42.0             15  0.391  1.0  28.0  0.0   
15  1374.0  2.0  0.0  24.0  42.0             16  0.188  1.0  25.0  0.0   
16  1368.0  0.0  0.0  28.0  42.0             17  0.400  0.0  29.0  0.0   
17  1357.0  4.0  0.0  21.0  42.0             18  0.500  3.0  25.0  0.0   
18  1352.0  0.0  0.0  26.0  42.0             19  0.190  0.0  27.0  0.0   
19  1346.0  0.0  0.0  15.0  42.0             20  0.615  0.0  17.0  0.0   
20  1341.0  2.0  0.0  31.0  42.0             21  0.269  0.0  31.0  0.0   
21  1335.0  2.0  0.0  26.0  42.0             22  0.308  0.0  28.0  0.0   
22  1330.0  0.0  0.0  24.0  42.0             23  0.250  2.0  26.0  0.0   
23  1323.0  2.0  0.0  19.0  42.0             24  0.400  2.0  22.0  0.0   
24  1318.0  1.0  0.0  25.0  42.0             25  0.294  2.0  28.0  0.0   
25  1315.0  1.0  0.0   4.0  42.0             26  0.500  0.0   4.0  0.0   
26  1313.0  0.0  0.0  27.0  42.0             27  0.222  1.0  28.0  0.0   
27  1308.0  1.0  0.0  33.0  42.0             28  0.290  0.0  33.0  0.0   
28  1303.0  0.0  1.0  26.0  42.0             29  0.292  1.0  27.0  0.0   
29  1297.0  2.0  0.0  21.0  42.0             30  0.278  1.0  23.0  1.0   
30  1290.0  0.0  0.0  23.0  42.0             31  0.227  1.0  25.0  0.0   
31  1284.0  0.0  0.0  22.0  42.0             32  0.389  0.0  22.0  0.0   
32  1279.0  0.0  0.0   3.0  42.0             33  0.000  0.0   3.0  0.0   
0   1459.0  0.0  0.0   4.0  42.0              1  0.333  0.0   4.0  0.0   
1   1458.0  0.0  0.0   7.0  42.0              2  0.667  0.0   7.0  0.0   
2   1454.0  0.0  0.0   4.0  42.0              3  1.000  1.0   5.0  0.0   
3   1452.0  0.0  0.0   3.0  42.0              4  0.000  0.0   3.0  0.0   
4   1449.0  0.0  0.0   3.0  42.0              5  0.000  1.0   4.0  0.0   
5   1446.0  0.0  0.0   3.0  42.0              6  1.000  0.0   3.0  0.0   
6   1445.0  0.0  0.0   5.0  42.0              7  0.400  0.0   5.0  0.0   
7   1394.0  0.0  0.0   5.0  42.0              8  0.500  0.0   5.0  0.0   
8   1392.0  0.0  0.0   3.0  42.0              9  0.000  0.0   3.0  0.0   
9   1390.0  0.0  0.0   5.0  42.0             10  0.333  1.0   6.0  0.0   
10  1387.0  0.0  0.0   3.0  42.0             11  0.000  0.0   3.0  0.0   
11  1386.0  0.0  0.0   3.0  42.0             12  0.500  0.0   3.0  0.0   
12  1382.0  0.0  0.0   5.0  42.0             13  0.500  0.0   5.0  0.0   
13  1381.0  0.0  0.0   1.0  42.0             14  0.000  0.0   1.0  0.0   
14  1377.0  0.0  0.0   1.0  42.0             15    NaN  0.0   1.0  0.0   
15  1375.0  0.0  0.0   3.0  42.0             16  0.000  0.0   3.0  0.0   
16  1371.0  0.0  0.0   3.0  42.0             17  0.000  0.0   3.0  0.0   
17  1370.0  0.0  0.0   3.0  42.0             18  0.000  0.0   3.0  0.0   
18  1367.0  0.0  0.0   4.0  42.0             19  0.333  0.0   4.0  0.0   
19  1365.0  0.0  0.0   4.0  42.0             20  0.333  0.0   4.0  0.0   
20  1364.

In [112]:
right = []
left = []

for index, row in return_frame.iterrows():
    if row.p_throws_x == 'R':
        right.append(row.key_mlbam)
#         print('right_ind: ', index)
    if row.p_throws_x == 'L':
        left.append(row.key_mlbam)
#         print('left_ind: ', index)
set(right).intersection(set(left))

{519381.0}

In [113]:
return_frame = return_frame[return_frame['key_mlbam'] != 519381.0]

In [114]:
return_frame

#days   2b   3b    ab   age  appearance_yr  babip   bb    bf   cs  \
0   1460.0  0.0  0.0  22.0  42.0              1  0.154  1.0  23.0  0.0   
1   1454.0  1.0  1.0  27.0  42.0              2  0.238  0.0  27.0  0.0   
2   1449.0  2.0  0.0  26.0  42.0              3  0.250  0.0  26.0  0.0   
3   1443.0  2.0  0.0  23.0  42.0              4  0.368  0.0  24.0  1.0   
4   1437.0  2.0  0.0  26.0  42.0              5  0.333  0.0  29.0  0.0   
5   1431.0  0.0  0.0  29.0  42.0              6  0.263  0.0  29.0  0.0   
6   1426.0  3.0  0.0  26.0  42.0              7  0.368  0.0  26.0  0.0   
7   1421.0  4.0  0.0  23.0  42.0              8  0.263  0.0  23.0  0.0   
8   1416.0  2.0  0.0  24.0  42.0              9  0.500  2.0  27.0  0.0   
9   1411.0  1.0  0.0  23.0  42.0             10  0.333  2.0  26.0  0.0   
10  1405.0  1.0  0.0  26.0  42.0             11  0.217  0.0  27.0  0.0   
11  1399.0  0.0  0.0  25.0  42.0             12  0.235  1.0  26.0  0.0   
12  1393.0  2.0  0.0  23.0  42.0             13  0.300  2.0  27.0  0.0   
13  1387.0  1.0  0.0  23.0  42.0             14  0.444  1.0  24.0  0.0   
14  1381.0  3.0  0.0  27.0  42.0             15  0.391  1.0  28.0  0.0   
15  1374.0  2.0  0.0  24.0  42.0             16  0.188  1.0  25.0  0.0   
16  1368.0  0.0  0.0  28.0  42.0             17  0.400  0.0  29.0  0.0   
17  1357.0  4.0  0.0  21.0  42.0             18  0.500  3.0  25.0  0.0   
18  1352.0  0.0  0.0  26.0  42.0             19  0.190  0.0  27.0  0.0   
19  1346.0  0.0  0.0  15.0  42.0             20  0.615  0.0  17.0  0.0   
20  1341.0  2.0  0.0  31.0  42.0             21  0.269  0.0  31.0  0.0   
21  1335.0  2.0  0.0  26.0  42.0             22  0.308  0.0  28.0  0.0   
22  1330.0  0.0  0.0  24.0  42.0             23  0.250  2.0  26.0  0.0   
23  1323.0  2.0  0.0  19.0  42.0             24  0.400  2.0  22.0  0.0   
24  1318.0  1.0  0.0  25.0  42.0             25  0.294  2.0  28.0  0.0   
25  1315.0  1.0  0.0   4.0  42.0             26  0.500  0.0   4.0  0.0   
26  1313.0  0.0  0.0  27.0  42.0             27  0.222  1.0  28.0  0.0   
27  1308.0  1.0  0.0  33.0  42.0             28  0.290  0.0  33.0  0.0   
28  1303.0  0.0  1.0  26.0  42.0             29  0.292  1.0  27.0  0.0   
29  1297.0  2.0  0.0  21.0  42.0             30  0.278  1.0  23.0  1.0   
30  1290.0  0.0  0.0  23.0  42.0             31  0.227  1.0  25.0  0.0   
31  1284.0  0.0  0.0  22.0  42.0             32  0.389  0.0  22.0  0.0   
32  1279.0  0.0  0.0   3.0  42.0             33  0.000  0.0   3.0  0.0   
0   1459.0  0.0  0.0   4.0  42.0              1  0.333  0.0   4.0  0.0   
1   1458.0  0.0  0.0   7.0  42.0              2  0.667  0.0   7.0  0.0   
2   1454.0  0.0  0.0   4.0  42.0              3  1.000  1.0   5.0  0.0   
3   1452.0  0.0  0.0   3.0  42.0              4  0.000  0.0   3.0  0.0   
4   1449.0  0.0  0.0   3.0  42.0              5  0.000  1.0   4.0  0.0   
5   1446.0  0.0  0.0   3.0  42.0              6  1.000  0.0   3.0  0.0   
6   1445.0  0.0  0.0   5.0  42.0              7  0.400  0.0   5.0  0.0   
7   1394.0  0.0  0.0   5.0  42.0              8  0.500  0.0   5.0  0.0   
8   1392.0  0.0  0.0   3.0  42.0              9  0.000  0.0   3.0  0.0   
9   1390.0  0.0  0.0   5.0  42.0             10  0.333  1.0   6.0  0.0   
10  1387.0  0.0  0.0   3.0  42.0             11  0.000  0.0   3.0  0.0   
11  1386.0  0.0  0.0   3.0  42.0             12  0.500  0.0   3.0  0.0   
12  1382.0  0.0  0.0   5.0  42.0             13  0.500  0.0   5.0  0.0   
13  1381.0  0.0  0.0   1.0  42.0             14  0.000  0.0   1.0  0.0   
14  1377.0  0.0  0.0   1.0  42.0             15    NaN  0.0   1.0  0.0   
15  1375.0  0.0  0.0   3.0  42.0             16  0.000  0.0   3.0  0.0   
16  1371.0  0.0  0.0   3.0  42.0             17  0.000  0.0   3.0  0.0   
17  1370.0  0.0  0.0   3.0  42.0             18  0.000  0.0   3.0  0.0   
18  1367.0  0.0  0.0   4.0  42.0             19  0.333  0.0   4.0  0.0   
19  1365.0  0.0  0.0   4.0  42.0             20  0.333  0.0   4.0  0.0   
20  1364.

In [115]:
return_frame.to_pickle('../pickles/sc_2015_unclean.pkl')